In [1]:
import pandas as pd
import numpy as np
import pandas_profiling as pp
import warnings
warnings.filterwarnings('ignore')

# Task 1 / Preprocessing

In [2]:
train = pd.read_csv('train.csv' , sep = '\t').drop( columns = 'Unnamed: 0')
test = pd.read_csv('test.csv', sep = '\t').drop( columns = 'Unnamed: 0')

print('size :' + str(train.shape))
print('trget % :' + str(train['0'].value_counts(normalize =True)[1]))
train.head()

size :(30500, 346)
trget % :0.17780327868852458


0  1  2  3  4  5  6         7  8  9 ...        336  337  338  339  340  \
0  1  1  0  0  0  0  0  0.090909  0  0 ...   0.221395    0    1    0    0   
1  1  1  0  0  1  0  0  0.090909  0  0 ...   0.241508    0    1    0    0   
2  0  1  0  0  1  0  0  0.090909  0  0 ...   0.123067    0    1    0    0   
3  0  1  0  0  1  0  0  0.136364  0  0 ...   0.296065    0    0    1    0   
4  0  1  0  0  1  0  0  0.136364  0  0 ...   0.178956    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.111111    1    1    1    0  
2  0.444444    1    1    1    1  
3  0.222222    1    1    1    0  
4  0.111111    1    1    1    1  

[5 rows x 346 columns]

In [3]:
for column in train.columns[1:]:
    delIndex = train.index[ (train[column] < test[column].min()) | (test[column].max() < train[column] )  ]
    train.drop( delIndex , inplace= True )
    
badCol = train.columns[[train[col].unique().size == 1 for col in train.columns ]]   
train.drop(columns = badCol , inplace = True )
test.drop(columns = badCol , inplace = True )
train.reset_index(drop=True , inplace= True)

print('size :' + str(train.shape))
print('trget % :' + str(train['0'].value_counts(normalize =True)[1]))
train.head()

size :(30254, 324)
trget % :0.17805909962319033


0  1  2  3  4  6         7  8  9  10 ...        336  337  338  339  340  \
0  1  1  0  0  0  0  0.090909  0  0   1 ...   0.221395    0    1    0    0   
1  1  1  0  0  1  0  0.090909  0  0   1 ...   0.241508    0    1    0    0   
2  0  1  0  0  1  0  0.090909  0  0   1 ...   0.123067    0    1    0    0   
3  0  1  0  0  1  0  0.136364  0  0   1 ...   0.296065    0    0    1    0   
4  0  1  0  0  1  0  0.136364  0  0   1 ...   0.178956    0    0    1    0   

        341  342  343  344  345  
0  0.222222    1    1    1    1  
1  0.111111    1    1    1    0  
2  0.444444    1    1    1    1  
3  0.222222    1    1    1    0  
4  0.111111    1    1    1    1  

[5 rows x 324 columns]

In [4]:
ppReportTrain = pp.ProfileReport(train)

In [5]:
ppReportTrain

In [6]:
train.drop(columns = ['9', '153'] , inplace = True )
test.drop(columns = ['9', '153'] , inplace = True )
corColumns = ppReportTrain.get_rejected_variables()
corColumns.remove('9')
corColumns.remove('153')

train size : 30254 | test size : 4022

train_size/test_size = 7.3

train/7 = 4222

4222 +-= 4022

=> 7 split

In [7]:
from sklearn.metrics import roc_auc_score
from sklearn.model_selection import StratifiedKFold , cross_val_score , GridSearchCV
X = train.drop(columns = '0')
y = train['0'].astype(int)
skf = StratifiedKFold(n_splits = int(train.shape[0]/test.shape[0] ), 
                      shuffle=True, random_state=42)

# Task 2 / LogisticRegression

In [8]:
from sklearn.linear_model import LogisticRegression

In [9]:
params = [  { 'C' : [0.01 , 0.03 , 0.05 ,0.1 , 0.5 , 1 , 10],'penalty' : ['l1'] ,'solver' : ['liblinear'] ,},
            { 'C' : [0.01 , 0.03 , 0.05 ,0.1 , 0.5 , 1 , 10],'solver' : ['sag'] ,'n_jobs' : [-1] ,}     ]

grid_search = GridSearchCV(
    estimator = LogisticRegression( random_state =  42 , class_weight= 'balanced' ) , 
    param_grid = params,
    cv=skf, 
    scoring='roc_auc', 
    verbose=1,
    n_jobs= -1,
)
grid_search.fit(X.drop(columns = corColumns) , y)
logReg_best = grid_search.best_estimator_
print('best params : ' + str(grid_search.best_params_))
print('expected score : ' + str(grid_search.best_score_))

Fitting 7 folds for each of 14 candidates, totalling 98 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:  3.2min
[Parallel(n_jobs=-1)]: Done  98 out of  98 | elapsed: 14.0min finished


best params : {'C': 0.1, 'n_jobs': -1, 'solver': 'sag'}
expected score : 0.7272928799820105


real score : 0.999

###### submission

In [10]:
logReg_best.fit(X.drop(columns = corColumns) , y)
pred = pd.Series(logReg_best.predict_proba( test.drop(columns = ['0']+ corColumns ))[:,1])
pred.to_csv('submission_LogReg.csv',header = True, index_label = True)

# Task 3 / Bagging LogisticRegression

In [11]:
from sklearn.ensemble import BaggingClassifier
from sklearn.linear_model import LogisticRegression

In [12]:
bg = BaggingClassifier( logReg_best ,
                        random_state= 42, 
                        n_jobs= -1       )

params = { "n_estimators" : [5 , 10 , 25 ]}
grid_search = GridSearchCV(
    estimator = bg, 
    param_grid = params,
    cv=skf, 
    scoring='roc_auc', 
    n_jobs= -1,
    verbose=1,  
)
grid_search.fit(X.drop(columns = corColumns ) , y)

baggingLogRer_best = grid_search.best_estimator_
print('best params : ' + str(grid_search.best_params_))
print('expected score : ' + str(grid_search.best_score_))

Fitting 7 folds for each of 3 candidates, totalling 21 fits


[Parallel(n_jobs=-1)]: Done  21 out of  21 | elapsed:  8.0min finished


best params : {'n_estimators': 25}
expected score : 0.7270960454425892


###### submission

In [13]:
baggingLogRer_best.fit(X.drop(columns = corColumns) ,y)
pred = pd.Series(baggingLogRer_best.predict_proba( test.drop(columns = ['0']+ corColumns ))[:,1] )
pred.to_csv('submission_LogReg_Bagging.csv',header = True, index_label = True)

# Task 4 / Random Forest

In [14]:
from sklearn.ensemble import RandomForestClassifier

In [15]:
params = {
          'criterion':['gini', 'entropy'],
          'max_depth': [5 ,10 , 20 , 50 , 100 , None] , 
          'min_samples_split': [ 5 ,  10 , 20 , 60 , 120] ,
          'max_features': [  100 , 200 ,None],
         }

grid_search = GridSearchCV(
    estimator =  RandomForestClassifier(n_estimators= 10 , 
                                        class_weight = 'balanced',
                                        random_state=42 , 
                                        n_jobs = -1 ), 
    param_grid = params,
    cv=3, 
    scoring='roc_auc', 
    n_jobs= -1,
    verbose=1,  
    error_score=1,  # warnings only
)
grid_search.fit(X , y)

randomForest_best = grid_search.best_estimator_
print('best params : ' + str(grid_search.best_params_))
print('best score : ' + str(grid_search.best_score_))

Fitting 3 folds for each of 180 candidates, totalling 540 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   15.6s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  2.9min
[Parallel(n_jobs=-1)]: Done 434 tasks      | elapsed:  8.0min
[Parallel(n_jobs=-1)]: Done 540 out of 540 | elapsed: 11.7min finished


best params : {'criterion': 'entropy', 'max_depth': 50, 'max_features': 200, 'min_samples_split': 120}
best score : 0.7188634775483947


In [16]:
randomForest_best.n_estimators = 100
score = cross_val_score(randomForest_best , X , y, cv =skf , scoring = 'roc_auc' , n_jobs =-1).mean()
print('expected score : ' + str(score))

expected score : 0.7340033660093752


###### submission

In [17]:
randomForest_best.fit(X , y)
pred = pd.Series(randomForest_best.predict_proba( test.drop(columns = '0'))[:,1])
pred.to_csv('submission_RandomForest.csv',header = True, index_label = True)

# Task 5 / Simple ensemble

In [18]:
models = {'baggingLogRer' : baggingLogRer_best ,'randomForest' :randomForest_best }

prediction = pd.DataFrame( columns = [name for name in models] , index = X.index)  

for trainVal , predVal in skf.split(X, y):
    for name in models:
        if name == 'logReg_best' or name == 'baggingLogRer_best' :
            models[name].fit( X.iloc[trainVal , X.columns != corColumns] , y[trainVal])
            prediction.loc[predVal , name]  = models[name].predict_proba( X.iloc[predVal ,X.columns !=corColumns])[:,1] 
        else:
            models[name].fit( X.iloc[trainVal] , y.iloc[trainVal])
            prediction.loc[predVal , name]= models[name].predict_proba(X.iloc[predVal])[:,1]


In [19]:
[roc_auc_score(y , prediction[model] ) for model in prediction.columns ]

[0.7263997651093945, 0.7339558573385052]

###### Simple averaging


In [20]:
from scipy.stats import rankdata
roc_auc_score(y, sum(rankdata(prediction[el]) for el in prediction) ) 

0.7377463364053513

###### Rank average

In [21]:
from scipy.stats import rankdata
roc_auc_score(y, sum(rankdata(prediction[el]) for el in prediction) ) 

0.7377463364053513

###### Weighted average


In [22]:
roc_auc_score(y,  (prediction['baggingLogRer' ]*0.35 + prediction['randomForest']*0.65 ) )

0.7387632406742837

###### submission

In [24]:
pred = pd.DataFrame() 
for modelName in models:
    if modelName == 'logReg_best' or modelName == 'baggingLogRer_best' :
        models[modelName].fit( X.drop(columns = corColumns), y)
        pred[modelName] = models[modelName].predict_proba(test.drop(columns =['0']+ corColumns))[:,1]
    else:
        models[modelName].fit( X, y)
        pred[modelName] = models[modelName].predict_proba(test.drop(columns ='0'))[:,1]
        
y_pred= pred['baggingLogRer' ]*0.35 + pred['randomForest']*0.65 
y_pred.to_csv('submission_Ensembl.csv',header = True, index_label = True)

# Task 6 / Stacking


In [25]:
X_stacking = pd.concat([X,prediction] ,axis =1  )
X_stacking.head()

1  2  3  4  6         7  8  10  12        13      ...       338  339  340  \
0  1  0  0  0  0  0.090909  0   1   1  0.461538      ...         1    0    0   
1  1  0  0  1  0  0.090909  0   1   1  0.187500      ...         1    0    0   
2  1  0  0  1  0  0.090909  0   1   1  0.200000      ...         1    0    0   
3  1  0  0  1  0  0.136364  0   1   1  0.000000      ...         0    1    0   
4  1  0  0  1  0  0.136364  0   1   1  0.650000      ...         0    1    0   

        341  342  343  344  345  baggingLogRer  randomForest  
0  0.222222    1    1    1    1       0.865593      0.753705  
1  0.111111    1    1    1    0       0.601869       0.55987  
2  0.444444    1    1    1    1       0.525623      0.505974  
3  0.222222    1    1    1    0         0.6485      0.519835  
4  0.111111    1    1    1    1       0.773682      0.764554  

[5 rows x 323 columns]

In [27]:
from sklearn.ensemble import ExtraTreesClassifier

In [29]:
params = {
          'criterion':['gini', 'entropy'],
          'max_depth': [4 , 6 ,8 ,12 , 16 ] , 
          'min_samples_split': [ 2 , 5 ,10 , 20 ] ,
          'max_features': [  100 , 200 , 300 ,None],
         }

grid_search = GridSearchCV(
    estimator =  ExtraTreesClassifier(n_estimators= 10 , 
                                      random_state=42 , 
                                      n_jobs = -1 ,
                                      class_weight = 'balanced'), 
    param_grid = params,
    cv= skf, 
    scoring='roc_auc', 
    n_jobs= -1,
    verbose=1,  
    error_score=1,  # warnings only
)
grid_search.fit(X_stacking , y)

extraTrees_final = grid_search.best_estimator_
print('best params : ' + str(grid_search.best_params_))
print('best score : ' + str(grid_search.best_score_))

Fitting 7 folds for each of 160 candidates, totalling 1120 fits


[Parallel(n_jobs=-1)]: Done  34 tasks      | elapsed:   16.1s
[Parallel(n_jobs=-1)]: Done 184 tasks      | elapsed:  2.1min
[Parallel(n_jobs=-1)]: Done 434 tasks      | elapsed:  7.7min
[Parallel(n_jobs=-1)]: Done 784 tasks      | elapsed: 15.0min
[Parallel(n_jobs=-1)]: Done 1120 out of 1120 | elapsed: 24.4min finished


best params : {'criterion': 'entropy', 'max_depth': 6, 'max_features': 300, 'min_samples_split': 2}
best score : 0.739115953120666


In [30]:
extraTrees_final.n_estimators= 100
score = cross_val_score(extraTrees_final , X_stacking, y, cv =skf , scoring = 'roc_auc' , n_jobs =-1 ).mean()
print('expected score : ' + str(score))

expected score : 0.7404132369391577


###### submission

In [31]:
pred_test = pd.DataFrame()  
for modelName in models:
    if modelName == 'logReg_best' or modelName == 'baggingLogRer_best' :
        models[modelName].fit( X.drop(columns = corColumns), y)
        pred_test[modelName] = models[modelName].predict_proba(test.drop(columns =['0']+ corColumns))[:,1]
    else:
        models[modelName].fit( X, y)
        pred_test[modelName] = models[modelName].predict_proba(test.drop(columns ='0'))[:,1]
test_stacking = pd.concat([test,pred_test] ,axis =1  )
test_stacking.head()

0  1  2  3  4  6         7  8  10  12      ...       338  339  340  \
0 NaN  1  0  0  1  0  0.136364  0   1   1      ...         1    0    0   
1 NaN  1  0  0  1  0  0.181818  0   1   1      ...         1    0    0   
2 NaN  1  0  0  0  0  0.090909  0   1   1      ...         1    0    0   
3 NaN  1  0  0  1  0  0.090909  0   1   1      ...         1    0    0   
4 NaN  1  0  0  1  0  0.090909  0   1   1      ...         0    1    0   

        341  342  343  344  345  baggingLogRer  randomForest  
0  0.222222    1    1    1    1       0.300208      0.465135  
1  0.000000    1    1    1    0       0.792917      0.642056  
2  0.222222    1    1    1    0       0.549107      0.574670  
3  0.000000    1    1    1    0       0.698876      0.692147  
4  0.000000    1    1    1    1       0.774696      0.830557  

[5 rows x 324 columns]

In [32]:
extraTrees_final.fit( X_stacking, y)
pred_final = extraTrees_final.predict_proba(test_stacking.drop(columns ='0'))[:,1]
pd.Series(pred_final).to_csv('submission_Stacking.csv',header = True, index_label = True)

# The End